In [1]:
# Benders decomposition for Fixed Charge Transportation Problem

import gurobipy as gp
from gurobipy import *
import numpy as np

In [2]:
#part a)
# solve with example in lecture
capacity = [5,8,7]
demand = [3,6,6,5]

locations = len(capacity)
customers = len(demand)

varcost = [[4,5,2,7],[5,8,6,2],[8,9,4,3]]
fixcost = [[2,10,1,5],[7,2,7,8],[4,0,3,9]]

bigM = [[min(capacity[i], demand[j]) for j in range(customers)] for i in range(locations)]

In [3]:
# Define Benders subproblem
        
def subproblem(model, where):
    if where == GRB.Callback.MIPSOL:
        v_y = model.cbGetSolution(model._y)
        print('\nCurrent y: ', v_y)
        
        LB = model.cbGetSolution(model._z)
        print('Current LB: ', LB, '\n')
        
        bsp = gp.Model("Subproblem") 
        #variables
        x = {}
        for i in range(locations):
            for j in range(customers):
                x[i,j] = bsp.addVar(obj=varcost[i][j])
        
        #unserved demand
        s = {}
        add_cost = np.max(varcost)*100
        for j in range(customers):
            s[j] = bsp.addVar(obj = add_cost)
        
        #demand constraint
        demand_constr = {} 
        for j in range(customers):
            demand_constr[j] = bsp.addConstr(sum(x[i,j] for i in range(locations)) + s[j]>= demand[j])
        
        #capacity constraint
        cap_constr = {}
        for i in range(locations):
            cap_constr[i] = bsp.addConstr(sum(x[i,j] for j in range(customers)) <= capacity[i])
        
        #logical constraint
        log_constr = {}
        for i in range(locations):
            for j in range(customers):
                log_constr[i,j] = bsp.addConstr(x[i,j] <= v_y[i,j] * min(capacity[i], demand[j]))
        
        bsp.optimize()
        
        
        #update ub and lb
        if bsp.objVal > LB:
            v = np.zeros(customers) #dual of demand constraints
            for j in range(customers):
                v[j] = demand_constr[j].pi #get dual value
            
            w = np.zeros((locations,customers)) #dual of logical constraints
            for i in range(locations):
                for j in range(customers):
                    w[i,j] = log_constr[i,j].pi
            
            u = np.zeros(locations) #dual of capacity constraints
            for i in range(locations):
                u[i] = cap_constr[i].pi
            
            cm = np.zeros((locations,customers)) #coefficient of y in master problem
            for i in range(locations):
                for j in range(customers):
                    cm[i,j] = fixcost[i][j] + min(capacity[i], demand[j]) * w[i,j]
            
            #print(bsp.objVal)
            #print(cm)
            #print(v)
            #print(w)
            #print(u)
            
                       
            model.cbLazy(model._z >= sum(demand[j] * v[j] for j in range(customers)) +   
                         sum(capacity[i] * u[i] for i in range(locations)) + 
                         sum(cm[i,j] * model._y[i,j] for i in range(locations) for j in range(customers)))
            #print(model._z >= sum(demand[j] * v[j] for j in range(customers)) +   
            #             sum(capacity[i] * u[i] for i in range(locations)) + 
            #             sum(cm[i,j] * model._y[i,j] for i in range(locations) for j in range(customers)))
        
        # save result of x from subproblem
        global transport
        for i in range(locations):
            for j in range(customers):
                transport[i,j] = x[i,j].x
        #print(transport)
        #print([s[j].x for j in range(customers)])
        #print(bsp.objVal)

        bsp.dispose()
                      

In [4]:
def masterproblem(MIPGap = None):
    global m
    
    # Relaxed Master problem function
    y = {}
    z = m.addVar(obj=1)                                                                           
    for i in range(locations):
        for j in range(customers):
            y[i,j] = m.addVar(vtype=GRB.BINARY)

    m.Params.lazyConstraints = 1
    m._y = y
    m._z = z
    
    if MIPGap is not None: m.Params.MIPGap = MIPGap
    m.optimize(subproblem)


    print("Objective: " + str(m.objVal))

    print("Solution:")
    import pandas as pd
    index = ['Source ' + str(x) for x in range(locations)]
    columns = ['Customer ' + str(x) for x in range(customers)]

    solution = pd.DataFrame(index=index, columns=columns)

    for i in range(locations):
        for j in range(customers):
            solution.iloc[i,j] = transport[i,j]

    print(solution)
    m.dispose()

In [5]:
# solve problem with Benders decomposition
transport = np.zeros((locations, customers)) # to save result of x from subproblem
m = gp.Model("Benders Fixed Charge Transportation Masterproblem") # to save model
masterproblem()

Using license file C:\Users\hadao\gurobi.lic
Academic license - for non-commercial use only
Changed value of parameter lazyConstraints to 1
   Prev: 0  Min: 0  Max: 1  Default: 0
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 0 rows, 13 columns and 0 nonzeros
Model fingerprint: 0xd03868d4
Variable types: 1 continuous, 12 integer (12 binary)
Coefficient statistics:
  Matrix range     [0e+00, 0e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [0e+00, 0e+00]

Current y:  {(0, 0): -0.0, (0, 1): -0.0, (0, 2): -0.0, (0, 3): -0.0, (1, 0): -0.0, (1, 1): -0.0, (1, 2): -0.0, (1, 3): -0.0, (2, 0): -0.0, (2, 1): -0.0, (2, 2): -0.0, (2, 3): -0.0}
Current LB:  0.0 

Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 19 rows, 16 columns and 40 nonzeros
Model fingerprint: 0x7635b122
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [2e+00, 9e+02]
  Bounds range     [0e+00, 0e+0

       4    2.7670000e+03   0.000000e+00   0.000000e+00      0s

Solved in 4 iterations and 0.01 seconds
Optimal objective  2.767000000e+03

Current y:  {(0, 0): 1.0, (0, 1): 1.0, (0, 2): 1.0, (0, 3): -0.0, (1, 0): 1.0, (1, 1): 1.0, (1, 2): 1.0, (1, 3): 1.0, (2, 0): -0.0, (2, 1): 1.0, (2, 2): 1.0, (2, 3): 1.0}
Current LB:  0.0 

Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 19 rows, 16 columns and 40 nonzeros
Model fingerprint: 0x07390468
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [2e+00, 9e+02]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+00, 8e+00]
Presolve removed 12 rows and 2 columns
Presolve time: 0.01s
Presolved: 7 rows, 14 columns, 24 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   1.150000e+01   0.000000e+00      0s
       6    8.3000000e+01   0.000000e+00   0.000000e+00      0s

Solved in 6 iterations and 0.01 seconds
Optimal objective  8.30000000

In [ ]:
#part b)
# solve with large example in database

In [6]:
file = open('43.txt','r')
data = file.readlines()

[locations, customers] = [int(x) for x in data[0].split(' ')]
capacity = [int(data[1].split(' ')[i]) for i in range(locations) ]
demand = [int(data[2].split(' ')[j]) for j in range(customers) ]

fixcost = [ [ int(data[i+3].split('   ')[j]) for j in range(customers) ] for i in range(locations)]
varcost = [ [ int(data[i+3+locations+1].split('    ')[j]) for j in range(customers) ] for i in range(locations)]

print(locations)
print(customers)
print(capacity)
print(demand)
fixcost

15
15
[20, 20, 20, 18, 18, 17, 17, 10, 10, 9, 9, 4, 4, 3, 3]
[20, 19, 19, 18, 17, 16, 16, 12, 11, 11, 7, 5, 5, 5, 1]


[[649, 685, 538, 791, 613, 205, 467, 569, 240, 219, 975, 765, 857, 677, 875],
 [798, 211, 701, 506, 431, 907, 945, 626, 979, 549, 466, 598, 231, 386, 887],
 [687, 261, 444, 264, 443, 946, 372, 648, 400, 781, 384, 557, 659, 996, 695],
 [335, 385, 967, 263, 423, 592, 939, 433, 521, 638, 835, 674, 454, 414, 775],
 [819, 340, 233, 889, 211, 854, 823, 438, 937, 394, 218, 224, 772, 344, 345],
 [307, 620, 845, 919, 223, 854, 656, 631, 896, 956, 322, 840, 258, 857, 639],
 [560, 959, 782, 417, 358, 589, 383, 753, 736, 390, 388, 587, 629, 469, 335],
 [375, 791, 720, 416, 251, 887, 235, 216, 694, 683, 821, 757, 894, 538, 217],
 [233, 415, 395, 605, 256, 964, 469, 431, 994, 255, 440, 719, 410, 374, 342],
 [285, 807, 245, 755, 654, 264, 999, 695, 674, 983, 233, 404, 835, 920, 782],
 [242, 483, 734, 378, 477, 732, 425, 625, 375, 285, 875, 855, 593, 948, 684],
 [899, 864, 443, 320, 751, 994, 529, 749, 335, 351, 810, 586, 968, 652, 659],
 [526, 530, 858, 426, 693, 724, 963, 360, 472, 846, 284, 421, 85

In [7]:
varcost

[[79, 68, 70, 25, 17, 65, 75, 67, 58, 61, 49, 34, 59, 33, 46],
 [39, 47, 43, 18, 55, 44, 41, 17, 73, 62, 56, 53, 41, 78, 80],
 [54, 43, 49, 74, 68, 55, 34, 74, 36, 73, 29, 75, 18, 20, 33],
 [24, 49, 19, 38, 50, 43, 56, 47, 79, 71, 69, 73, 78, 78, 24],
 [47, 18, 46, 25, 30, 69, 59, 68, 72, 49, 21, 39, 43, 36, 65],
 [20, 40, 26, 25, 28, 32, 39, 60, 77, 23, 53, 75, 73, 42, 60],
 [35, 81, 55, 25, 56, 39, 48, 78, 81, 50, 75, 38, 54, 39, 35],
 [77, 69, 61, 67, 64, 39, 48, 71, 52, 53, 58, 66, 26, 68, 45],
 [49, 20, 81, 57, 40, 73, 32, 19, 27, 30, 68, 22, 25, 53, 58],
 [46, 38, 35, 74, 73, 68, 58, 55, 29, 31, 32, 43, 34, 41, 30],
 [56, 40, 80, 75, 79, 29, 39, 35, 23, 63, 60, 16, 56, 35, 65],
 [76, 56, 68, 52, 42, 23, 18, 33, 31, 73, 19, 20, 22, 79, 74],
 [43, 59, 78, 16, 19, 44, 56, 43, 57, 16, 42, 37, 72, 29, 47],
 [45, 44, 54, 38, 79, 44, 67, 26, 22, 47, 38, 57, 34, 45, 31],
 [50, 16, 67, 80, 76, 31, 48, 43, 71, 44, 64, 21, 72, 40, 22]]

In [ ]:
# solve problem with Benders decomposition
transport = np.zeros((locations, customers)) # to save result of x from subproblem
m = gp.Model("Benders Fixed Charge Transportation Masterproblem") # to save model
masterproblem(0.05)

Changed value of parameter lazyConstraints to 1
   Prev: 0  Min: 0  Max: 1  Default: 0
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 0 rows, 226 columns and 0 nonzeros
Model fingerprint: 0x01ab2a9e
Variable types: 1 continuous, 225 integer (225 binary)
Coefficient statistics:
  Matrix range     [0e+00, 0e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [0e+00, 0e+00]

Current y:  {(0, 0): -0.0, (0, 1): -0.0, (0, 2): -0.0, (0, 3): -0.0, (0, 4): -0.0, (0, 5): -0.0, (0, 6): -0.0, (0, 7): -0.0, (0, 8): -0.0, (0, 9): -0.0, (0, 10): -0.0, (0, 11): -0.0, (0, 12): -0.0, (0, 13): -0.0, (0, 14): -0.0, (1, 0): -0.0, (1, 1): -0.0, (1, 2): -0.0, (1, 3): -0.0, (1, 4): -0.0, (1, 5): -0.0, (1, 6): -0.0, (1, 7): -0.0, (1, 8): -0.0, (1, 9): -0.0, (1, 10): -0.0, (1, 11): -0.0, (1, 12): -0.0, (1, 13): -0.0, (1, 14): -0.0, (2, 0): -0.0, (2, 1): -0.0, (2, 2): -0.0, (2, 3): -0.0, (2, 4): -0.0, (2, 5): -0.0, (2, 6): -0.0, (2, 7): -0.0, 

Optimize a model with 255 rows, 240 columns and 690 nonzeros
Model fingerprint: 0xffbbb97b
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [2e+01, 8e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 2e+01]
Presolve removed 225 rows and 0 columns
Presolve time: 0.01s
Presolved: 30 rows, 240 columns, 465 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   9.150000e+01   0.000000e+00      0s
      37    4.1550000e+03   0.000000e+00   0.000000e+00      0s

Solved in 37 iterations and 0.01 seconds
Optimal objective  4.155000000e+03
<gurobi.TempConstr: <gurobi.LinExpr: C0> >= <gurobi.LinExpr: 4455.0 + 649.0 C1 + 685.0 C2 + 538.0 C3 + 791.0 C4 + 613.0 C5 + 205.0 C6 + 467.0 C7 + 569.0 C8 + 240.0 C9 + 219.0 C10 + 975.0 C11 + 765.0 C12 + 857.0 C13 + 677.0 C14 + 875.0 C15 + 798.0 C16 + 211.0 C17 + 701.0 C18 + 506.0 C19 + 431.0 C20 + 907.0 C21 + 945.0 C22 + 626.0 C23 + 979.0 C24 + 549.0 C25 + 466.0 C26 +

      37    4.1550000e+03   0.000000e+00   0.000000e+00      0s

Solved in 37 iterations and 0.01 seconds
Optimal objective  4.155000000e+03
<gurobi.TempConstr: <gurobi.LinExpr: C0> >= <gurobi.LinExpr: 4455.0 + 649.0 C1 + 685.0 C2 + 538.0 C3 + 791.0 C4 + 613.0 C5 + 205.0 C6 + 467.0 C7 + 569.0 C8 + 240.0 C9 + 219.0 C10 + 975.0 C11 + 765.0 C12 + 857.0 C13 + 677.0 C14 + 875.0 C15 + 798.0 C16 + 211.0 C17 + 701.0 C18 + 506.0 C19 + 431.0 C20 + 907.0 C21 + 945.0 C22 + 626.0 C23 + 979.0 C24 + 549.0 C25 + 466.0 C26 + 598.0 C27 + 231.0 C28 + 386.0 C29 + 887.0 C30 + 687.0 C31 + 261.0 C32 + 444.0 C33 + 264.0 C34 + 443.0 C35 + 946.0 C36 + 372.0 C37 + 648.0 C38 + 400.0 C39 + 781.0 C40 + 384.0 C41 + 557.0 C42 + 659.0 C43 + 996.0 C44 + 695.0 C45 + 335.0 C46 + 385.0 C47 + 769.0 C48 + 263.0 C49 + 423.0 C50 + 592.0 C51 + 939.0 C52 + 433.0 C53 + 521.0 C54 + 638.0 C55 + 835.0 C56 + 674.0 C57 + 454.0 C58 + 414.0 C59 + 775.0 C60 + 819.0 C61 + 340.0 C62 + 233.0 C63 + 889.0 C64 + 211.0 C65 + 854.0 C66 + 823.0 

Optimize a model with 255 rows, 240 columns and 690 nonzeros
Model fingerprint: 0xed038301
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [2e+01, 8e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 2e+01]
Presolve removed 255 rows and 240 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    1.3137800e+06   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  1.313780000e+06
<gurobi.TempConstr: <gurobi.LinExpr: C0> >= <gurobi.LinExpr: 1474200.0 + -159771.0 C1 + -151923.0 C2 + -152032.0 C3 + -144559.0 C4 + -136798.0 C5 + -128355.0 C6 + -127933.0 C7 + -95827.0 C8 + -88222.0 C9 + -88210.0 C10 + -55382.0 C11 + -39565.0 C12 + -39348.0 C13 + -39658.0 C14 + -7179.0 C15 + -160422.0 C16 + -152796.0 C17 + -152382.0 C18 + -144970.0 C19 + -136334.0 C20 + -127989.0 C21 + -127999.0 C22 + -96370.0 C23 + -87318.0 C24 + -87869

Optimize a model with 255 rows, 240 columns and 690 nonzeros
Model fingerprint: 0x5add2ad3
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [2e+01, 8e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 2e+01]
Presolve removed 255 rows and 240 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    1.4742000e+06   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  1.474200000e+06
<gurobi.TempConstr: <gurobi.LinExpr: C0> >= <gurobi.LinExpr: 1474200.0 + -159771.0 C1 + -151923.0 C2 + -152032.0 C3 + -144559.0 C4 + -136798.0 C5 + -128355.0 C6 + -127933.0 C7 + -95827.0 C8 + -88222.0 C9 + -88210.0 C10 + -55382.0 C11 + -39565.0 C12 + -39348.0 C13 + -39658.0 C14 + -7179.0 C15 + -160422.0 C16 + -152796.0 C17 + -152382.0 C18 + -144970.0 C19 + -136334.0 C20 + -127989.0 C21 + -127999.0 C22 + -96370.0 C23 + -87318.0 C24 + -87869

...

Exception ignored in: 'gurobipy.callbackstub'
Traceback (most recent call last):
  File "callback.pxi", line 180, in gurobipy.CallbackClass.callback
  File "<ipython-input-13-bd341ff70259>", line 4, in subproblem
KeyboardInterrupt


 11706555 4949320     cutoff   49      12377.9928 12018.1732  2.91%  10.8 9925s
 11712665 4951117 12188.0302   67   16 12377.9928 12018.2420  2.91%  10.8 9930s


KeyboardInterrupt: 

Exception ignored in: 'gurobipy.callbackstub'
Traceback (most recent call last):
  File "callback.pxi", line 180, in gurobipy.CallbackClass.callback
  File "<ipython-input-13-bd341ff70259>", line 4, in subproblem
KeyboardInterrupt


 11718499 4953130 12127.0641   57   19 12377.9928 12018.3016  2.91%  10.8 9935s
